In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn import preprocessing
import random
# REFINED libraries
import pickle
import scipy.misc
import sys

import Toolbox 
from Toolbox import *
import math
from scipy import stats

import Utils
import utils_nn
import model
from model import *
from utils_nn import *
from Utils import *
#import utils_tl_cind
from utils_tl_cind import *


from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import OneHotEncoder
from lifelines.utils import concordance_index
from sklearn.model_selection import KFold

import torch 
from torch import nn
import torch.optim as optim
import torch.nn.functional as F
from torch.nn.init import kaiming_uniform_
from torch.nn.init import xavier_uniform_

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
device = "cpu"

In [ ]:
Dir = 'TCGA/'

RNAseq_PD = pd.read_csv(Dir+'combined_rnaseq.csv') # RNAseq data for each patient
Cancers = RNAseq_PD['cancer_type'].unique().tolist()
GuanRank_all_PD = pd.read_csv(Dir+'whole_data.csv') # Survival (OS) and GuanRank data for each patient

In [ ]:
Guan_train_all, Guan_test_all = GuanRankSplit(GuanRank_all_PD)

In [ ]:
Disease = ['GBMLGG','KIPAN', 'HNSC', 'GBM', 'LUAD', 'LUSC', 'BLCA', 'BRCA', 'COADREAD']


In [ ]:
from sklearn import linear_model
from sksurv.ensemble import RandomSurvivalForest
from sksurv.linear_model import CoxnetSurvivalAnalysis, CoxPHSurvivalAnalysis

In [ ]:
def surv_conv(dataset, censored, surv):
    y_surv = np.empty(dtype=[(censored, np.bool), (surv, np.float64)],shape=dataset.shape[0])
    y_surv[censored] = (dataset[censored] == True).values
    y_surv[surv] = dataset[surv].values
    return y_surv
#Y_PD = Surv_PD[['patient.vital_status','times']]
#Y_PD = surv_conv(Y_PD, 'patient.vital_status','times')

In [ ]:
RNAseq_PD = RNAseq_PD.drop_duplicates(subset='Patient_ID', keep="first")
Shots = [0,10,20,30,40]
All_res = []
for cns in Disease:
    print("Cancer type: " + cns)
    for shot_size in Shots:
        print("SHOT: ", shot_size)
        cind_ls = []
        for fold in range(5):
            clf = linear_model.Lasso(alpha=0.001,warm_start = True)
            #clf = RandomSurvivalForest()
            #clf = RandomForestRegressor(n_estimators=500, warm_start = True)
            print("Fold: " , fold)

            data = Dataset(Guan_train_all, Guan_test_all, RNAseq_PD, fold, cns, Dir, 'TSNE')
            data.read_REFINED()
            data.Split_Data(device)

            X_Test_disease  = data.X_REFINED_Test_disease.reshape(-1,105*105)
            X_Train_disease  = data.X_REFINED_Train_disease.reshape(-1,105*105)
            X_Test_rest  = data.X_REFINED_Test_rest.reshape(-1,105*105)
            X_Train_rest  = data.X_REFINED_Train_rest.reshape(-1,105*105)
            
            
            Y_train_rest = surv_conv(data.Guan_train_rest, 'OS','OS.time')
            Y_test_rest = surv_conv(data.Guan_test_rest, 'OS','OS.time')
            Y_train_disease = surv_conv(data.Guan_train_disease, 'OS','OS.time')
            Y_test_disease = surv_conv(data.Guan_test_disease, 'OS','OS.time')
            
            #clf.fit(X_Train_rest, Y_train_rest)
            #cind = clf.score(X_Test_rest, Y_test_rest)
            # if model is regression guan
            clf.fit(X_Train_rest, data.Guan_train_rest['GuanRank'].values)
            y_pred_rest = clf.predict(X_Test_rest)
            #cind = RF.score(X_test, Y_test)
            cind = concordance_index(data.Guan_test_rest['OS.time'].values, -y_pred_rest, data.Guan_test_rest['OS'].values)
            print("C-index of pretrain: ", cind)
            
            if shot_size!=0:
                clf.fit(X_Train_disease[:shot_size], data.Guan_train_disease['GuanRank'].values[:shot_size])
                #clf.fit(X_Train_disease[:shot_size], Y_train_disease[:shot_size])
            #cind_disease = clf.score(X_Test_disease, Y_test_disease)
           
            y_pred_disease = clf.predict(X_Test_disease)
            cind_disease = concordance_index(data.Guan_test_disease['OS.time'].values, -y_pred_disease, data.Guan_test_disease['OS'].values)
            print("C-index of disease: ", cind_disease)
            
            
            p_value_disease = StatistTest(cind_disease, y_pred_disease, data.Guan_test_disease, n_bootstrap = 1000)
            print("p_value: " , p_value_disease)
            cind_ls.append(cind_disease)
            del clf
        Avg_Cind = pd.DataFrame(data = np.array([np.mean(cind_ls), np.std(cind_ls)]).reshape(1,-1), columns = ['Mean', 'STD'], index = [cns])
        All_res.append(Avg_Cind)
    Avg_Cind = pd.concat(All_res)
    print(Avg_Cind)